<a href="https://colab.research.google.com/github/lphuong304/CS116.M11/blob/main/Practice%20In%20Class/19520227/BaiTapLamThem/19520227_BTLT.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

<h1 align="center"><strong>BÀI TẬP  - 12/10/2021</strong></h1>
<h1 align="center"><strong>LẬP TRÌNH PYTHON CHO MÁY HỌC CS116.M11 - NÉN DỮ LIỆU VIDEO BẰNG PCA</strong></h1>

# GIỚI THIỆU:

1. Họ và tên: Nguyễn Ngọc Lan Phương
2. MSSV: 19520227 - KHMT2019
3. Lớp: CS116.M11
4. Bài tập: Nén dữ liệu video bằng PCA.
5. Ngày thực hiện: 12/10/2021

#get dữ liệu video

In [ ]:
!gdown --id 1cC6betu5w-h3YWjBJThW7UVoWUf9klf_

Downloading...
From: https://drive.google.com/uc?id=1cC6betu5w-h3YWjBJThW7UVoWUf9klf_
To: /content/test10s.mp4
100% 1.11M/1.11M [00:00<00:00, 73.2MB/s]


# import packages

In [ ]:
!pip install sk-video
!pip install ffmpeg
!pip install thinkx
!pgrep -lf python

     |████████████████████████████████| 2.3 MB 4.7 MB/s 
  Created wheel for ffmpeg: filename=ffmpeg-1.4-py3-none-any.whl size=6083 sha256=31e8ef4617c93ec8eda98db92ca233244f05e419f5f66487872b79a38143cc39
  Stored in directory: /root/.cache/pip/wheels/64/80/6e/caa3e16deb0267c3cbfd36862058a724144e19fdb9eb03af0f
Successfully built ffmpeg
     |████████████████████████████████| 41 kB 124 kB/s 
  Created wheel for thinkx: filename=thinkx-1.1.3-py3-none-any.whl size=59942 sha256=5df5c7eb009e136622b0777e1a28b20d65da71ff0a6f1cfb9810d86328991a4a
  Stored in directory: /root/.cache/pip/wheels/48/28/47/bcd375ed163bf0ab5364d98faca0626adae06e4976ac93f8ae
Successfully built thinkx
52 jupyter-noteboo
64 python3
84 python3


In [ ]:
import numpy as np
import cv2
import skvideo.io
from google.colab.patches import cv2_imshow
import warnings
warnings.filterwarnings('ignore')
from sklearn.decomposition import PCA
import ffmpeg
import thinkdsp
from IPython.display import Audio  
from scipy.io import wavfile
import moviepy.editor as mp
from IPython.display import clear_output, Image
import base64

Imageio: 'ffmpeg-linux64-v3.3.1' was not found on your computer; downloading it now.
Try 1. Download from https://github.com/imageio/imageio-binaries/raw/master/ffmpeg/ffmpeg-linux64-v3.3.1 (43.8 MB)
Downloading: 8192/45929032 bytes (0.0%)1736704/45929032 bytes (3.8%)4415488/45929032 bytes (9.6%)7012352/45929032 bytes (15.3%)9371648/45929032 bytes (20.4%)11771904/45929032 bytes (25.6%)13508608/45929032 bytes (29.4%)15433728/45929032 bytes (33.6%)17768448/45929032 bytes (38.7%)19742720/45929032 bytes (43.0%)21790720/45929032 bytes (47.4%)23240704/45929032 bytes (50.6%)25370624/45929032 bytes (55.2%)277

#get audio from video

In [ ]:
getClip = mp.VideoFileClip(r"/content/test10s.mp4")

In [ ]:
getClip

In [ ]:
getClip.audio.write_audiofile(r"audio.mp3")

[MoviePy] Writing audio in audio.mp3


100%|██████████| 229/229 [00:00<00:00, 601.83it/s]

[MoviePy] Done.


In [ ]:
!ffmpeg -i /content/audio.mp3 -acodec pcm_u8 -ar 22050 /content/audio.wav

ffmpeg version 3.4.8-0ubuntu0.2 Copyright (c) 2000-2020 the FFmpeg developers
  built with gcc 7 (Ubuntu 7.5.0-3ubuntu1~18.04)
  configuration: --prefix=/usr --extra-version=0ubuntu0.2 --toolchain=hardened --libdir=/usr/lib/x86_64-linux-gnu --incdir=/usr/include/x86_64-linux-gnu --enable-gpl --disable-stripping --enable-avresample --enable-avisynth --enable-gnutls --enable-ladspa --enable-libass --enable-libbluray --enable-libbs2b --enable-libcaca --enable-libcdio --enable-libflite --enable-libfontconfig --enable-libfreetype --enable-libfribidi --enable-libgme --enable-libgsm --enable-libmp3lame --enable-libmysofa --enable-libopenjpeg --enable-libopenmpt --enable-libopus --enable-libpulse --enable-librubberband --enable-librsvg --enable-libshine --enable-libsnappy --enable-libsoxr --enable-libspeex --enable-libssh --enable-libtheora --enable-libtwolame --enable-libvorbis --enable-libvpx --enable-libwavpack --enable-libwebp --enable-libx265 --enable-libxml2 --enable-libxvid --enable-lib

#read audio

In [ ]:
rate, testAudio = wavfile.read('/content/audio.wav') 
print("Demesion of Original audio: {}".format(testAudio.shape))
Audio(data=testAudio[:, 0], rate=rate)

Demesion of Original audio: (228218, 2)


#reshape audio

In [ ]:
getAudio = testAudio[:,0]
size = len(getAudio)
getMod = 512 - np.mod(size, 512)
getPad = np.lib.pad(getAudio, (0, getMod), 'constant', constant_values=0)

# Reshape the signal to have 512 dimensions
reshapeAudio = getPad.reshape((len(getPad) // 512, 512))

#reduce demension of audio using pca and reconstruct

In [ ]:
# getAudio = testAudio[:,0]
# getAudio.shape
# vận dụng kỹ thuật pca để giảm số chiều dữ liệu array audio
pca = PCA(n_components=64)
pca.fit(reshapeAudio)
transformAudio = pca.transform(reshapeAudio)

#khôi phục lại array audio ban đầu
reconstructAudio = pca.inverse_transform(transformAudio).reshape((len(getPad)))
print("Demesion of inversed audio : {}".format(reconstructAudio.shape))
Audio(data=reconstructAudio[:], rate=rate)

Demesion of inversed audio : (228352,)


#save audio

In [ ]:
with open('/content/result.wav', 'wb') as f:
    f.write(reconstructAudio[:].data)

#read video, display and get information

In [ ]:
getClip.ipython_display()

100%|██████████| 311/311 [00:01<00:00, 219.47it/s]


In [ ]:
videogen = skvideo.io.vread('/content/test10s.mp4')
frames = videogen.shape[0]
height, width = videogen.shape[1],videogen.shape[2]
depth = videogen.shape[3]
print("Frames number of video: {}".format(frames))
print("Size of each frame: {}x{}".format(height, width))
print("Depth of each frame: {}".format(depth))
videogen = skvideo.io.vreader('/content/test10s.mp4')
feature = []
for frame in videogen:
  frame = frame.flatten()
  feature.append(frame)

Frames number of video: 308
Size of each frame: 360x640
Depth of each frame: 3


In [ ]:
feature = np.array(feature)
print("Demesion of original video: {}".format(feature.shape))

Demesion of original video: (308, 691200)


#splting frames of video in R,G,B arrays and apply PCA to individual array

In [ ]:
def applyPCA(img, n_components):
  B,G,R = cv2.split(img)
  pca = PCA(n_components=n_components)

  transformRed = pca.fit_transform(R)
  invertRed = pca.inverse_transform(transformRed)

  transformGreen = pca.fit_transform(G)
  invertGreen = pca.inverse_transform(transformGreen)
  
  transformBlue = pca.fit_transform(B)
  invertBlue = pca.inverse_transform(transformBlue)

  frame_compressed = (np.dstack((invertRed,invertGreen,invertBlue))).astype(np.uint8)
  return frame_compressed

In [ ]:
capture = cv2.VideoCapture('/content/test10s.mp4')
fourcc = cv2.VideoWriter_fourcc(*'XVID')
output = cv2.VideoWriter('output.avi', fourcc, frames//10, (width,height),True)
i = 0
while (capture.isOpened()):
  ret, fr = capture.read()
 
  if ret == True:
    pcaFr = applyPCA(fr, 64)
    result = cv2.cvtColor(pcaFr,cv2.COLOR_BGR2RGB)
    output.write(result)
    if cv2.waitKey(1) & 0xFF == ord('q'):
      break
  else:
    break

capture.release()
output.release()
cv2.destroyAllWindows()

#add reduced demension audio to reduced demesion video 

In [ ]:
!ffmpeg -i /content/output.avi -i /content/audio.wav  -map 0:v -map 1:a -c:v copy -shortest /content/result.avi

ffmpeg version 3.4.8-0ubuntu0.2 Copyright (c) 2000-2020 the FFmpeg developers
  built with gcc 7 (Ubuntu 7.5.0-3ubuntu1~18.04)
  configuration: --prefix=/usr --extra-version=0ubuntu0.2 --toolchain=hardened --libdir=/usr/lib/x86_64-linux-gnu --incdir=/usr/include/x86_64-linux-gnu --enable-gpl --disable-stripping --enable-avresample --enable-avisynth --enable-gnutls --enable-ladspa --enable-libass --enable-libbluray --enable-libbs2b --enable-libcaca --enable-libcdio --enable-libflite --enable-libfontconfig --enable-libfreetype --enable-libfribidi --enable-libgme --enable-libgsm --enable-libmp3lame --enable-libmysofa --enable-libopenjpeg --enable-libopenmpt --enable-libopus --enable-libpulse --enable-librubberband --enable-librsvg --enable-libshine --enable-libsnappy --enable-libsoxr --enable-libspeex --enable-libssh --enable-libtheora --enable-libtwolame --enable-libvorbis --enable-libvpx --enable-libwavpack --enable-libwebp --enable-libx265 --enable-libxml2 --enable-libxvid --enable-lib

#display video result

In [ ]:
videoOutput = mp.VideoFileClip('/content/result.avi')
videoOutput.ipython_display()

100%|██████████| 310/310 [00:01<00:00, 209.49it/s]
